In [1]:
!git clone https://github.com/EleutherAI/lm-evaluation-harness
%cd lm-evaluation-harness
!pip install -q -e .

Cloning into 'lm-evaluation-harness'...
remote: Enumerating objects: 10915, done.
remote: Counting objects: 100% (3423/3423), done.
remote: Compressing objects: 100% (513/513), done.
remote: Total 10915 (delta 3072), reused 3003 (delta 2908), pack-reused 7492
Receiving objects: 100% (10915/10915), 12.46 MiB | 17.52 MiB/s, done.
Resolving deltas: 100% (7253/7253), done.
/content/lm-evaluation-harness
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 474.6/474.6 kB 31.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 73.6/73.6 kB 9.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.5/79.5 kB 11.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.8/56.8 kB 6.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 222.3/222.3 kB 26.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.1/10.1 MB 67.7 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build

In [21]:
!git clone https://github.com/TurkuNLP/finnish-generative-model-eval.git

Cloning into 'finnish-generative-model-eval'...
remote: Enumerating objects: 715, done.
remote: Counting objects: 100% (426/426), done.
remote: Compressing objects: 100% (243/243), done.
remote: Total 715 (delta 201), reused 269 (delta 93), pack-reused 289
Receiving objects: 100% (715/715), 1.60 MiB | 3.11 MiB/s, done.
Resolving deltas: 100% (321/321), done.


In [22]:
import os

tasks = []
for folder in os.listdir("finnish-generative-model-eval/benchmark_tasks"):
    print(folder)
    if (os.path.exists(f"finnish-generative-model-eval/benchmark_tasks/{folder}/task.json")) and (folder != "cause_and_effect"):
        os.rename(f"finnish-generative-model-eval/benchmark_tasks/{folder}/task.json", f"lm_eval/datasets/bigbench_resources/{folder}.json")
        tasks.append(folder)
    else:
        for sub_folder in os.listdir(f"finnish-generative-model-eval/benchmark_tasks/{folder}"):
            if os.path.exists(f"finnish-generative-model-eval/benchmark_tasks/{folder}/{sub_folder}/task.json"):
                os.rename(f"finnish-generative-model-eval/benchmark_tasks/{folder}/{sub_folder}/task.json", f"lm_eval/datasets/bigbench_resources/{folder}_{sub_folder}.json")
                tasks.append(f"{folder}_{sub_folder}")

emotions
sentence_ambiguity
misconceptions
similarities_abstraction
cause_and_effect
intent_recognition
paraphrase
hhh_alignment
general_knowledge
analogies
arithmetic
empirical_judgments


In [23]:
print(",".join([f"bigbench_{t}" for t in tasks]))

bigbench_emotions,bigbench_sentence_ambiguity,bigbench_misconceptions,bigbench_similarities_abstraction,bigbench_cause_and_effect_one_sentence_no_prompt,bigbench_cause_and_effect_one_sentence,bigbench_cause_and_effect_two_sentences,bigbench_intent_recognition,bigbench_paraphrase,bigbench_hhh_alignment_helpful,bigbench_hhh_alignment_other,bigbench_hhh_alignment_honest,bigbench_hhh_alignment_harmless,bigbench_general_knowledge,bigbench_analogies,bigbench_arithmetic_3_digit_subtraction,bigbench_arithmetic_3_digit_addition,bigbench_arithmetic_2_digit_subtraction,bigbench_arithmetic_1_digit_multiplication,bigbench_arithmetic_1_digit_division,bigbench_arithmetic_5_digit_addition,bigbench_arithmetic_4_digit_division,bigbench_arithmetic_4_digit_subtraction,bigbench_arithmetic_1_digit_addition,bigbench_arithmetic_2_digit_multiplication,bigbench_arithmetic_1_digit_subtraction,bigbench_arithmetic_5_digit_division,bigbench_arithmetic_5_digit_multiplication,bigbench_arithmetic_3_digit_multiplicatio

Manually set context len to 2048

In [10]:
%%writefile /content/lm-evaluation-harness/lm_eval/models/gpt2.py
import torch
import transformers
from typing import Optional, Union
from lm_eval.base import BaseLM


def _get_dtype(
    dtype: Union[str, torch.dtype]
) -> torch.dtype:
    """Converts `dtype` from `str` to torch.dtype when possible. Does not use an instantiated HF AutoConfig"""
    if isinstance(dtype, str) and dtype != "auto":
        # Convert `str` args torch dtype: `float16` -> `torch.float16`
        _torch_dtype = getattr(torch, dtype)
    else:
        _torch_dtype = dtype
    return _torch_dtype


class HFLM(BaseLM):
    def __init__(
        self,
        device="cuda",
        pretrained="gpt2",
        revision="main",
        low_cpu_mem_usage=None,
        subfolder=None,
        tokenizer=None,
        batch_size=1,
        load_in_8bit: Optional[bool] = False,
        trust_remote_code: Optional[bool] = False,
        dtype: Optional[Union[str, torch.dtype]]="auto",
    ):
        super().__init__()

        assert isinstance(device, str)
        assert isinstance(pretrained, str)
        assert isinstance(batch_size, (int, str))

        device_list = set(
            ["cuda", "cpu"] + [f"cuda:{i}" for i in range(torch.cuda.device_count())]
        )
        if device and device in device_list:
            self._device = torch.device(device)
            print(f"Using device '{device}'")
        else:
            print("Device not specified")
            print(f"Cuda Available? {torch.cuda.is_available()}")
            self._device = (
                torch.device("cuda")
                if torch.cuda.is_available()
                else torch.device("cpu")
            )

        # TODO: update this to be less of a hack once subfolder is fixed in HF
        revision = revision + ("/" + subfolder if subfolder is not None else "")

        self.gpt2 = transformers.AutoModelForCausalLM.from_pretrained(
            pretrained,
            load_in_8bit=load_in_8bit,
            low_cpu_mem_usage=low_cpu_mem_usage,
            revision=revision,
            torch_dtype=_get_dtype(dtype),
            trust_remote_code=trust_remote_code,
        ).to(self.device)
        self.gpt2.eval()

        self.tokenizer = transformers.AutoTokenizer.from_pretrained(
            pretrained if tokenizer is None else tokenizer,
            revision=revision,
            trust_remote_code=trust_remote_code,
        )

        self.vocab_size = self.tokenizer.vocab_size

        if isinstance(
            self.tokenizer, (transformers.GPT2Tokenizer, transformers.GPT2TokenizerFast)
        ):
            assert self.tokenizer.encode("hello\n\nhello") == [
                31373,
                198,
                198,
                31373,
            ], self.tokenizer.encode("hello\n\nhello")

        # setup for automatic batch size detection
        if batch_size == "auto":
            self.batch_size_per_gpu = batch_size
        else:
            self.batch_size_per_gpu = int(batch_size)

    @property
    def eot_token_id(self):
        # we use EOT because end of *text* is more accurate for what we're doing than end of *sentence*
        return self.tokenizer.eos_token_id

    @property
    def max_length(self):
        try:
            return self.gpt2.config.n_ctx
        except AttributeError:
            # gptneoconfig doesn't have n_ctx apparently
            return 2048
            #return self.gpt2.config.max_position_embeddings

    @property
    def max_gen_toks(self):
        return 256

    @property
    def batch_size(self):
        # TODO: fix multi-gpu
        return self.batch_size_per_gpu  # * gpus

    @property
    def device(self):
        # TODO: fix multi-gpu
        return self._device

    def tok_encode(self, string: str):
        return self.tokenizer.encode(string, add_special_tokens=False)

    def tok_decode(self, tokens):
        return self.tokenizer.decode(tokens)

    def _model_call(self, inps):
        """
        inps: a torch tensor of shape [batch, sequence]
        the size of sequence may vary from call to call

        returns: a torch tensor of shape [batch, sequence, vocab] with the
        logits returned from the model
        """
        with torch.no_grad():
            return self.gpt2(inps)[0]

    def _model_generate(self, context, max_length, eos_token_id):
        generation_kwargs = {"do_sample": False, "max_length": max_length}
        if eos_token_id is not None:
            generation_kwargs['eos_token_id'] = eos_token_id
            generation_kwargs['pad_token_id'] = eos_token_id # setting eos_token_id as pad token
        return self.gpt2.generate(context, **generation_kwargs)


# for backwards compatibility
GPT2LM = HFLM


Overwriting /content/lm-evaluation-harness/lm_eval/models/gpt2.py


In [28]:
!python main.py \
    --model hf-causal \
    --model_args pretrained=TurkuNLP/gpt3-finnish-small \
    --tasks bigbench_emotions,bigbench_sentence_ambiguity,bigbench_misconceptions,bigbench_similarities_abstraction,bigbench_cause_and_effect_one_sentence_no_prompt,bigbench_cause_and_effect_one_sentence,bigbench_cause_and_effect_two_sentences,bigbench_intent_recognition,bigbench_paraphrase,bigbench_hhh_alignment_helpful,bigbench_hhh_alignment_other,bigbench_hhh_alignment_honest,bigbench_hhh_alignment_harmless,bigbench_general_knowledge,bigbench_analogies,bigbench_arithmetic_3_digit_subtraction,bigbench_arithmetic_3_digit_addition,bigbench_arithmetic_2_digit_subtraction,bigbench_arithmetic_1_digit_multiplication,bigbench_arithmetic_1_digit_division,bigbench_arithmetic_5_digit_addition,bigbench_arithmetic_4_digit_division,bigbench_arithmetic_4_digit_subtraction,bigbench_arithmetic_1_digit_addition,bigbench_arithmetic_2_digit_multiplication,bigbench_arithmetic_1_digit_subtraction,bigbench_arithmetic_5_digit_division,bigbench_arithmetic_5_digit_multiplication,bigbench_arithmetic_3_digit_multiplication,bigbench_arithmetic_5_digit_subtraction,bigbench_arithmetic_4_digit_addition,bigbench_arithmetic_2_digit_addition,bigbench_arithmetic_4_digit_multiplication,bigbench_arithmetic_2_digit_division,bigbench_arithmetic_3_digit_division,bigbench_empirical_judgments \
    --device cuda:0 \
    --output_path results/gpt3_finnish_small_bigbench.json

2023-06-08 11:56:14.385733: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
Selected Tasks: ['bigbench_analogies', 'bigbench_arithmetic_1_digit_addition', 'bigbench_arithmetic_1_digit_division', 'bigbench_arithmetic_1_digit_multiplication', 'bigbench_arithmetic_1_digit_subtraction', 'bigbench_arithmetic_2_digit_addition', 'bigbench_arithmetic_2_digit_division', 'bigbench_arithmetic_2_digit_multiplication', 'bigbench_arithmetic_2_digit_subtraction', 'bigbench_arithmetic_3_digit_addition', 'bigbench_arithmetic_3_digit_division', 'bigbench_arithmetic_3_digit_multiplication', 'bigbench_arithmetic_3_digit_subtraction', 'bigbench_arithmetic_4_digit_addition', 'bigbench_arithmetic_4_digit_division', 'bigbench_arithmetic_4_digit_multiplication', 'bigbench_arithmetic_4_digit_subtraction', 'bigbench_arithmetic_5_digit_addition', 'bigbench_arithmetic_5_digit_division', 'bigbench_arithmetic_5_digit_multiplication', 'bigbench_arithmetic_5_digit_subtra

In [29]:
!python main.py \
    --model hf-causal \
    --model_args pretrained=TurkuNLP/gpt3-finnish-medium \
    --tasks bigbench_emotions,bigbench_sentence_ambiguity,bigbench_misconceptions,bigbench_similarities_abstraction,bigbench_cause_and_effect_one_sentence_no_prompt,bigbench_cause_and_effect_one_sentence,bigbench_cause_and_effect_two_sentences,bigbench_intent_recognition,bigbench_paraphrase,bigbench_hhh_alignment_helpful,bigbench_hhh_alignment_other,bigbench_hhh_alignment_honest,bigbench_hhh_alignment_harmless,bigbench_general_knowledge,bigbench_analogies,bigbench_arithmetic_3_digit_subtraction,bigbench_arithmetic_3_digit_addition,bigbench_arithmetic_2_digit_subtraction,bigbench_arithmetic_1_digit_multiplication,bigbench_arithmetic_1_digit_division,bigbench_arithmetic_5_digit_addition,bigbench_arithmetic_4_digit_division,bigbench_arithmetic_4_digit_subtraction,bigbench_arithmetic_1_digit_addition,bigbench_arithmetic_2_digit_multiplication,bigbench_arithmetic_1_digit_subtraction,bigbench_arithmetic_5_digit_division,bigbench_arithmetic_5_digit_multiplication,bigbench_arithmetic_3_digit_multiplication,bigbench_arithmetic_5_digit_subtraction,bigbench_arithmetic_4_digit_addition,bigbench_arithmetic_2_digit_addition,bigbench_arithmetic_4_digit_multiplication,bigbench_arithmetic_2_digit_division,bigbench_arithmetic_3_digit_division,bigbench_empirical_judgments \
    --device cuda:0 \
    --output_path results/gpt3_finnish_medium_bigbench.json

2023-06-08 12:07:36.224439: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
Selected Tasks: ['bigbench_analogies', 'bigbench_arithmetic_1_digit_addition', 'bigbench_arithmetic_1_digit_division', 'bigbench_arithmetic_1_digit_multiplication', 'bigbench_arithmetic_1_digit_subtraction', 'bigbench_arithmetic_2_digit_addition', 'bigbench_arithmetic_2_digit_division', 'bigbench_arithmetic_2_digit_multiplication', 'bigbench_arithmetic_2_digit_subtraction', 'bigbench_arithmetic_3_digit_addition', 'bigbench_arithmetic_3_digit_division', 'bigbench_arithmetic_3_digit_multiplication', 'bigbench_arithmetic_3_digit_subtraction', 'bigbench_arithmetic_4_digit_addition', 'bigbench_arithmetic_4_digit_division', 'bigbench_arithmetic_4_digit_multiplication', 'bigbench_arithmetic_4_digit_subtraction', 'bigbench_arithmetic_5_digit_addition', 'bigbench_arithmetic_5_digit_division', 'bigbench_arithmetic_5_digit_multiplication', 'bigbench_arithmetic_5_digit_subtra

In [31]:
!python main.py \
    --model hf-causal \
    --model_args pretrained=TurkuNLP/gpt3-finnish-large \
    --tasks bigbench_emotions,bigbench_sentence_ambiguity,bigbench_misconceptions,bigbench_similarities_abstraction,bigbench_cause_and_effect_one_sentence_no_prompt,bigbench_cause_and_effect_one_sentence,bigbench_cause_and_effect_two_sentences,bigbench_intent_recognition,bigbench_paraphrase,bigbench_hhh_alignment_helpful,bigbench_hhh_alignment_other,bigbench_hhh_alignment_honest,bigbench_hhh_alignment_harmless,bigbench_general_knowledge,bigbench_analogies,bigbench_arithmetic_3_digit_subtraction,bigbench_arithmetic_3_digit_addition,bigbench_arithmetic_2_digit_subtraction,bigbench_arithmetic_1_digit_multiplication,bigbench_arithmetic_1_digit_division,bigbench_arithmetic_5_digit_addition,bigbench_arithmetic_4_digit_division,bigbench_arithmetic_4_digit_subtraction,bigbench_arithmetic_1_digit_addition,bigbench_arithmetic_2_digit_multiplication,bigbench_arithmetic_1_digit_subtraction,bigbench_arithmetic_5_digit_division,bigbench_arithmetic_5_digit_multiplication,bigbench_arithmetic_3_digit_multiplication,bigbench_arithmetic_5_digit_subtraction,bigbench_arithmetic_4_digit_addition,bigbench_arithmetic_2_digit_addition,bigbench_arithmetic_4_digit_multiplication,bigbench_arithmetic_2_digit_division,bigbench_arithmetic_3_digit_division,bigbench_empirical_judgments \
    --device cuda:0 \
    --output_path results/gpt3_finnish_large_bigbench.json

2023-06-08 12:27:00.388671: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
Selected Tasks: ['bigbench_analogies', 'bigbench_arithmetic_1_digit_addition', 'bigbench_arithmetic_1_digit_division', 'bigbench_arithmetic_1_digit_multiplication', 'bigbench_arithmetic_1_digit_subtraction', 'bigbench_arithmetic_2_digit_addition', 'bigbench_arithmetic_2_digit_division', 'bigbench_arithmetic_2_digit_multiplication', 'bigbench_arithmetic_2_digit_subtraction', 'bigbench_arithmetic_3_digit_addition', 'bigbench_arithmetic_3_digit_division', 'bigbench_arithmetic_3_digit_multiplication', 'bigbench_arithmetic_3_digit_subtraction', 'bigbench_arithmetic_4_digit_addition', 'bigbench_arithmetic_4_digit_division', 'bigbench_arithmetic_4_digit_multiplication', 'bigbench_arithmetic_4_digit_subtraction', 'bigbench_arithmetic_5_digit_addition', 'bigbench_arithmetic_5_digit_division', 'bigbench_arithmetic_5_digit_multiplication', 'bigbench_arithmetic_5_digit_subtra

In [33]:
!python main.py \
    --model hf-causal \
    --model_args pretrained=TurkuNLP/gpt3-finnish-xl \
    --tasks bigbench_emotions,bigbench_sentence_ambiguity,bigbench_misconceptions,bigbench_similarities_abstraction,bigbench_cause_and_effect_one_sentence_no_prompt,bigbench_cause_and_effect_one_sentence,bigbench_cause_and_effect_two_sentences,bigbench_intent_recognition,bigbench_paraphrase,bigbench_hhh_alignment_helpful,bigbench_hhh_alignment_other,bigbench_hhh_alignment_honest,bigbench_hhh_alignment_harmless,bigbench_general_knowledge,bigbench_analogies,bigbench_arithmetic_3_digit_subtraction,bigbench_arithmetic_3_digit_addition,bigbench_arithmetic_2_digit_subtraction,bigbench_arithmetic_1_digit_multiplication,bigbench_arithmetic_1_digit_division,bigbench_arithmetic_5_digit_addition,bigbench_arithmetic_4_digit_division,bigbench_arithmetic_4_digit_subtraction,bigbench_arithmetic_1_digit_addition,bigbench_arithmetic_2_digit_multiplication,bigbench_arithmetic_1_digit_subtraction,bigbench_arithmetic_5_digit_division,bigbench_arithmetic_5_digit_multiplication,bigbench_arithmetic_3_digit_multiplication,bigbench_arithmetic_5_digit_subtraction,bigbench_arithmetic_4_digit_addition,bigbench_arithmetic_2_digit_addition,bigbench_arithmetic_4_digit_multiplication,bigbench_arithmetic_2_digit_division,bigbench_arithmetic_3_digit_division,bigbench_empirical_judgments \
    --device cuda:0 \
    --output_path results/gpt3_finnish_xl_bigbench.json

2023-06-08 13:05:47.506695: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
Selected Tasks: ['bigbench_analogies', 'bigbench_arithmetic_1_digit_addition', 'bigbench_arithmetic_1_digit_division', 'bigbench_arithmetic_1_digit_multiplication', 'bigbench_arithmetic_1_digit_subtraction', 'bigbench_arithmetic_2_digit_addition', 'bigbench_arithmetic_2_digit_division', 'bigbench_arithmetic_2_digit_multiplication', 'bigbench_arithmetic_2_digit_subtraction', 'bigbench_arithmetic_3_digit_addition', 'bigbench_arithmetic_3_digit_division', 'bigbench_arithmetic_3_digit_multiplication', 'bigbench_arithmetic_3_digit_subtraction', 'bigbench_arithmetic_4_digit_addition', 'bigbench_arithmetic_4_digit_division', 'bigbench_arithmetic_4_digit_multiplication', 'bigbench_arithmetic_4_digit_subtraction', 'bigbench_arithmetic_5_digit_addition', 'bigbench_arithmetic_5_digit_division', 'bigbench_arithmetic_5_digit_multiplication', 'bigbench_arithmetic_5_digit_subtra

In [ ]:
#!/bin/bash
#SBATCH --nodes=1
#SBATCH --ntasks-per-node=1
#SBATCH --cpus-per-task=32
#SBATCH --mem=256G
#SBATCH -p eap
#SBATCH -t 2-0:00:00
#SBATCH --gpus-per-node=mi250:1
#SBATCH --exclusive=user
#SBATCH --hint=nomultithread
#SBATCH --account=project_462000241
#SBATCH -o logs/%j.out
#SBATCH -e logs/%j.err

source /pfs/lustrep2/scratch/project_462000241/muennighoff/lmevallatest/venv/bin/activate

cd /pfs/lustrep2/scratch/project_462000241/muennighoff/lmevallatest/lm-evaluation-harness

python main.py \
--model hf-causal \
--model_args pretrained=gpt3-finnish-large \
--tasks bigbench_emotions,bigbench_sentence_ambiguity,bigbench_misconceptions,bigbench_similarities_abstraction,bigbench_cause_and_effect_one_sentence_no_prompt,bigbench_cause_and_effect_one_sentence,bigbench_cause_and_effect_two_sentences,bigbench_intent_recognition,bigbench_paraphrase,bigbench_hhh_alignment_helpful,bigbench_hhh_alignment_other,bigbench_hhh_alignment_honest,bigbench_hhh_alignment_harmless,bigbench_general_knowledge,bigbench_analogies,bigbench_arithmetic_3_digit_subtraction,bigbench_arithmetic_3_digit_addition,bigbench_arithmetic_2_digit_subtraction,bigbench_arithmetic_1_digit_multiplication,bigbench_arithmetic_1_digit_division,bigbench_arithmetic_5_digit_addition,bigbench_arithmetic_4_digit_division,bigbench_arithmetic_4_digit_subtraction,bigbench_arithmetic_1_digit_addition,bigbench_arithmetic_2_digit_multiplication,bigbench_arithmetic_1_digit_subtraction,bigbench_arithmetic_5_digit_division,bigbench_arithmetic_5_digit_multiplication,bigbench_arithmetic_3_digit_multiplication,bigbench_arithmetic_5_digit_subtraction,bigbench_arithmetic_4_digit_addition,bigbench_arithmetic_2_digit_addition,bigbench_arithmetic_4_digit_multiplication,bigbench_arithmetic_2_digit_division,bigbench_arithmetic_3_digit_division,bigbench_empirical_judgments \
--device cuda:0 \
--output_path results/gpt3_finnish_large_bigbench.json

##### Old

In [ ]:
!wget https://raw.githubusercontent.com/TurkuNLP/finnish-generative-model-eval/main/benchmark_tasks/analogies/task.json
!wget https://raw.githubusercontent.com/TurkuNLP/finnish-generative-model-eval/main/benchmark_tasks/arithmetic/task.json

!wget https://raw.githubusercontent.com/TurkuNLP/finnish-generative-model-eval/main/benchmark_tasks/emotions/task.json



!mv task.json lm_eval/datasets/bigbench_resources/emotions.json

--2023-06-05 18:56:01--  https://raw.githubusercontent.com/TurkuNLP/finnish-generative-model-eval/main/benchmark_tasks/emotions/task.json
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.111.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 45898 (45K) [text/plain]
Saving to: ‘task.json’

task.json           100%[===================>]  44.82K  --.-KB/s    in 0.001s  

2023-06-05 18:56:01 (38.4 MB/s) - ‘task.json’ saved [45898/45898]

--2023-06-05 18:56:36--  https://raw.githubusercontent.com/TurkuNLP/finnish-generative-model-eval/main/benchmark_tasks/emotions/task.json
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awa

In [ ]:
!python main.py \
    --model hf-causal \
    --model_args pretrained=EleutherAI/pythia-160m,revision=step100000,dtype="float" \
    --tasks bigbench_emotions \
    --device cuda:0 \
    --limit 5

2023-06-05 18:56:42.277494: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
Selected Tasks: ['bigbench_emotions']
Using device 'cuda:0'
Task: bigbench_emotions; number of docs: 160
Task: bigbench_emotions; document 0; context prompt (starting on next line):
Perustunteet ovat hämmästys, ilo, inho, luottamus, odotus, pelko, suru ja suuttumus. Nimeä perustunne seuraavista teksteistä.
Teksti: Toivoin, että olisit hänelle esimerkkinä.
Perustunne: 
(end of prompt on previous line)
Requests: [Req_loglikelihood('Perustunteet ovat hämmästys, ilo, inho, luottamus, odotus, pelko, suru ja suuttumus. Nimeä perustunne seuraavista teksteistä.\nTeksti: Toivoin, että olisit hänelle esimerkkinä.\nPerustunne: ', 'hämmästys')[0]
, Req_loglikelihood('Perustunteet ovat hämmästys, ilo, inho, luottamus, odotus, pelko, suru ja suuttumus. Nimeä perustunne seuraavista teksteistä.\nTeksti: Toivoin, että olisit hänelle esimerkkinä.\nPerustunne: ', 'ilo')[0]
, Req_log

In [ ]:
!python main.py \
    --model hf-causal \
    --model_args pretrained=EleutherAI/pythia-160m,revision=step100000,dtype="float" \
    --tasks bigbench_geometric_shapes \
    --device cuda:0 \
    --limit 5

2023-06-05 18:57:33.651774: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
Selected Tasks: ['bigbench_geometric_shapes']
Using device 'cuda:0'
Task: bigbench_geometric_shapes; number of docs: 359
Task: bigbench_geometric_shapes; document 0; context prompt (starting on next line):

Q: This SVG path element <path d="M 59.18,98.64 L 65.20,80.96 L 57.00,68.63 L 55.43,56.00 M 55.43,56.00 L 67.76,43.69 M 67.76,43.69 L 80.38,62.66 L 92.36,80.67 L 59.18,98.64"/> draws a 
  choice: sector
  choice: heptagon
  choice: octagon
  choice: circle
  choice: rectangle
  choice: hexagon
  choice: triangle
  choice: line
  choice: kite
  choice: pentagon
A: 
(end of prompt on previous line)
Requests: [Req_loglikelihood('\nQ: This SVG path element <path d="M 59.18,98.64 L 65.20,80.96 L 57.00,68.63 L 55.43,56.00 M 55.43,56.00 L 67.76,43.69 M 67.76,43.69 L 80.38,62.66 L 92.36,80.67 L 59.18,98.64"/> draws a \n  choice: sector\n  choice: heptagon\n  choice: oc

In [ ]:
!python main.py \
    --model hf-causal \
    --model_args pretrained=TurkuNLP/gpt3-finnish-small \
    --tasks bigbench_geometric_shapes \
    --device cuda:0

In [ ]:
!git clone https://huggingface.co/TurkuNLP/gpt3-finnish-small